In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/cubesat/test_dataset_v5/good/6.jpg
/kaggle/input/cubesat/test_dataset_v5/good/5.jpg
/kaggle/input/cubesat/test_dataset_v5/good/8.jpg
/kaggle/input/cubesat/test_dataset_v5/good/0.jpg
/kaggle/input/cubesat/test_dataset_v5/good/1.jpg
/kaggle/input/cubesat/test_dataset_v5/good/17.jpg
/kaggle/input/cubesat/test_dataset_v5/good/15.jpg
/kaggle/input/cubesat/test_dataset_v5/good/4.jpg
/kaggle/input/cubesat/test_dataset_v5/good/3.jpg
/kaggle/input/cubesat/test_dataset_v5/good/14.jpg
/kaggle/input/cubesat/test_dataset_v5/good/2.jpg
/kaggle/input/cubesat/test_dataset_v5/good/3 (2).jpg
/kaggle/input/cubesat/test_dataset_v5/bad/20.jpg
/kaggle/input/cubesat/test_dataset_v5/bad/6.jpg
/kaggle/input/cubesat/test_dataset_v5/bad/5.jpg
/kaggle/input/cubesat/test_dataset_v5/bad/10.jpg
/kaggle/input/cubesat/test_dataset_v5/bad/0.jpg
/kaggle/input/cubesat/test_dataset_v5/bad/9.jpg
/kaggle/input/cubesat/test_dataset_v5/bad/1.jpg
/kaggle/input/cubesat/test_dataset_v5/bad/16.jpg
/kaggle/input/cube

In [2]:
import matplotlib.pyplot as plt
import tensorflow as tf 
from tensorflow import keras 
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Activation, Conv2D, MaxPooling2D, Flatten, Dropout, BatchNormalization
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from sklearn.metrics import precision_recall_curve, roc_curve, accuracy_score, confusion_matrix, precision_score, recall_score
from sklearn.decomposition import PCA
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt 
import seaborn as sns 
plt.style.use('fivethirtyeight')
import pickle 
import os 
import numpy as np
import cv2 
%matplotlib inline
import pandas.util.testing as tm

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:20: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.


In [3]:
labels = ['bad', 'good']
img_size = 100
def get_training_data(data_dir):
    data = [] 
    for label in labels: 
        path = os.path.join(data_dir, label)
        class_num = labels.index(label)
        for img in os.listdir(path):
            try:
                img_arr = cv2.imread(os.path.join(path, img),cv2.IMREAD_GRAYSCALE)
                resized_arr = cv2.resize(img_arr, (img_size, img_size))
                data.append([resized_arr, class_num])
            except Exception as e:
                print(e)
    return np.array(data)

In [4]:
train = get_training_data('../input/cubesat/training_dataset_v3')
test = get_training_data('../input/cubesat/test_dataset_v5')

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:15: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  from ipykernel import kernelapp as app


In [5]:
bad = 0 
good = 0 

for i, j in train:
    if j == 0:
        bad+=1
    else:
        good+=1
        
print('Bad:', bad)
print('good:', good)
print('Bad - Good:', bad-good)

Bad: 30000
good: 30000
Bad - Good: 0


In [6]:
X = []
y = []

for feature, label in train:
    X.append(feature)
    y.append(label)

for feature, label in test:
    X.append(feature)
    y.append(label)
    


# resize data for deep learning 
X = np.array(X).reshape(-1, img_size, img_size, 1)
y = np.array(y)

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=32)

In [7]:
X_train = X_train / 255
X_test = X_test / 255

In [8]:
print(X_train.shape)

(48024, 100, 100, 1)


In [9]:
'''model = keras.Sequential([
  keras.layers.Conv2D(input_shape=(100,100,3), filters=8, kernel_size=3, 
                      strides=2, activation='relu', name='Conv1'),
  keras.layers.Flatten(),
  keras.layers.Dense(2, activation=tf.nn.softmax, name='Softmax')
])
model.summary()

testing = False
epochs = 15

model.compile(optimizer='adam', 
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])
model.fit(X_train, y_train, epochs=epochs)

test_loss, test_acc = model.evaluate(X_test, y_test)
print('\nTest accuracy: {}'.format(test_acc))
'''

"model = keras.Sequential([\n  keras.layers.Conv2D(input_shape=(100,100,3), filters=8, kernel_size=3, \n                      strides=2, activation='relu', name='Conv1'),\n  keras.layers.Flatten(),\n  keras.layers.Dense(2, activation=tf.nn.softmax, name='Softmax')\n])\nmodel.summary()\n\ntesting = False\nepochs = 15\n\nmodel.compile(optimizer='adam', \n              loss='sparse_categorical_crossentropy',\n              metrics=['accuracy'])\nmodel.fit(X_train, y_train, epochs=epochs)\n\ntest_loss, test_acc = model.evaluate(X_test, y_test)\nprint('\nTest accuracy: {}'.format(test_acc))\n"

In [10]:
from keras.utils.np_utils import to_categorical # convert to one-hot-encoding
from keras.models import Sequential
from keras.layers import Dense, Dropout, Flatten, Conv2D, MaxPool2D, BatchNormalization
from keras.optimizers import Adam
from keras.preprocessing.image import ImageDataGenerator
from keras.callbacks import LearningRateScheduler

In [11]:
model = Sequential()

model.add(Conv2D(filters = 16, kernel_size = (3, 3), activation='relu',
                 input_shape = (100, 100, 1)))
model.add(BatchNormalization())
model.add(Conv2D(filters = 16, kernel_size = (3, 3), activation='relu'))
model.add(BatchNormalization())
#model.add(Conv2D(filters = 16, kernel_size = (3, 3), activation='relu'))
#model.add(BatchNormalization())
model.add(MaxPool2D(strides=(2,2)))
model.add(Dropout(0.25))

model.add(Conv2D(filters = 32, kernel_size = (3, 3), activation='relu'))
model.add(BatchNormalization())
model.add(Conv2D(filters = 32, kernel_size = (3, 3), activation='relu'))
model.add(BatchNormalization())
#model.add(Conv2D(filters = 32, kernel_size = (3, 3), activation='relu'))
#model.add(BatchNormalization())
model.add(MaxPool2D(strides=(2,2)))
model.add(Dropout(0.25))

model.add(Flatten())
model.add(Dense(512, activation='relu'))
model.add(Dropout(0.25))
model.add(Dense(1024, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(2, activation='softmax'))

testing = False
epochs = 15

model.compile(optimizer='adam', 
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])
model.fit(X_train, y_train, epochs=epochs)

test_loss, test_acc = model.evaluate(X_test, y_test)
print('\nTest accuracy: {}'.format(test_acc))

Epoch 1/15
1501/1501 [==============================] - 673s 448ms/step - loss: 1.0145 - accuracy: 0.7099
Epoch 2/15
1501/1501 [==============================] - 673s 448ms/step - loss: 0.4096 - accuracy: 0.8183
Epoch 3/15
1501/1501 [==============================] - 674s 449ms/step - loss: 0.3647 - accuracy: 0.8424
Epoch 4/15
1501/1501 [==============================] - 678s 452ms/step - loss: 0.3428 - accuracy: 0.8510
Epoch 5/15
1501/1501 [==============================] - 680s 453ms/step - loss: 0.3348 - accuracy: 0.8590
Epoch 6/15
1501/1501 [==============================] - 682s 454ms/step - loss: 0.3182 - accuracy: 0.8633
Epoch 7/15
1501/1501 [==============================] - 684s 456ms/step - loss: 0.3054 - accuracy: 0.8697
Epoch 8/15
1501/1501 [==============================] - 689s 459ms/step - loss: 0.2888 - accuracy: 0.8784
Epoch 9/15
1501/1501 [==============================] - 690s 460ms/step - loss: 0.2819 - accuracy: 0.8811
Epoch 10/15
1501/1501 [=======================

In [12]:
model.compile(loss='categorical_crossentropy', optimizer = Adam(lr=1e-4), metrics=["accuracy"])

In [13]:
print(model.predict(X_test))

[[1.0885664e-03 9.9891138e-01]
 [9.9996090e-01 3.9060931e-05]
 [2.7540058e-02 9.7245997e-01]
 ...
 [9.7622365e-01 2.3776330e-02]
 [4.0453836e-01 5.9546167e-01]
 [9.6071357e-01 3.9286450e-02]]
